# Άσκηση: Σύγκριση των Gausian Naive Bayes, Logistic Regression και kNN στo Pima Indians Diabetes dataset
![1889 Photograph shows half-length portrait of two Pima Indians, facing front, wearing bead necklaces.](https://i.pinimg.com/236x/60/05/76/600576905d4ad5bb1a9c3e3387b397ca--pima-indians-native-american-indians.jpg "1889 Photograph shows half-length portrait of two Pima Indians, facing front, wearing bead necklaces.")

Διαβάστε το ["pima-indians-diabetes.data.csv"](https://raw.githubusercontent.com/jbrownlee/Datasets/master/pima-indians-diabetes.data.csv) σε ένα numpy array data και ξεχωρίστε features και labels.

Για 40% test set: 
1. υπολογίστε την πρόβλεψη του Gaussian Naive Bayes με τη μέθοδο predict(). 
2. υπολογίστε την πρόβλεψη της λογιστικής παλινδρόμισης με τη μέθοδο predict().
3. για έναν ταξινομητή kNN, με 3-fold cross validation και με μετρική 'f1_weighted' υπολογίστε το βέλτιστο k στο train set (maximum k=50). 
4. εκτυπώστε με την "classification_report" τα precision, recall, f1, support για τον GNB, τη λογιστική παλινδρόμηση και τον kNN με βέλτιστο k που προέκυψε από το cross validation.

Συζήτηση: στο συγκεκριμένο dataset: 
- ποιος ταξινομητής είναι "καλύτερος";
- τι μπορούμε να κάνουμε για να βελτιωθεί η απόδοση του κάθε ταξινομητή;

In [ ]:
import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/jbrownlee/Datasets/master/pima-indians-diabetes.data.csv', header=None)
labels_df = df.iloc[:, [8]] 
features_df = df.iloc[:, 0:8]

import numpy as np
features = features_df.values
labels = labels_df.values.reshape(768,)
print(labels.shape)

In [ ]:
from sklearn.model_selection import train_test_split
train, test, train_labels, test_labels = train_test_split(features, labels, test_size=0.4)

In [ ]:
from sklearn.naive_bayes import GaussianNB
gnb = GaussianNB()

gnb.fit(train, train_labels)
gnb_pred = gnb.predict(test)

In [ ]:
from sklearn.linear_model import LogisticRegression
lr = LogisticRegression(solver='saga', max_iter=500)
lr.fit(train, train_labels)
lr_pred = gnb.predict(test)

In [ ]:
from sklearn.model_selection import cross_val_score

# φτιάχνουμε μια λίστα από το 1 έως το 50
myList = list(range(1,50))
# Κρατάμε μόνο τα περιττά k
neighbors = list(filter(lambda x: x % 2 != 0, myList))
# empty list that will hold cv scores
cv_scores = []
# perform 5-fold cross validation
for k in neighbors:
    knn_opt = KNeighborsClassifier(n_neighbors=k)
    scores = cross_val_score(knn_opt, train, train_labels, cv=3, scoring='f1_weighted')
    cv_scores.append(scores.mean())

In [ ]:
# Κάνουμε update την matplotlib, ίσως χρειαστεί restart του runtime
!pip install --upgrade matplotlib

# Κάνουμε import την matplotplib
import matplotlib.pyplot as plt

# το σφάλμα είναι το αντίστροφο της πιστότητας
mean_error = [1 - x for x in cv_scores]

# plot misclassification error vs k
plt.plot(neighbors, mean_error)
plt.xlabel('Number of Neighbors K')
plt.ylabel('Misclassification Error')
plt.show()

# determining best k
optimal_k = neighbors[mean_error.index(min(mean_error))]
print("The optimal number of neighbors (calculated in the training set) is %d" % optimal_k)

In [ ]:
knn_opt = KNeighborsClassifier(n_neighbors=5)
knn_opt.fit(train, train_labels)
knn_opt_pred = knn.predict(test)

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(test_labels, gnb_pred))

In [ ]:
print(classification_report(test_labels, knn_opt_pred))

In [ ]:
print(classification_report(test_labels, lr_pred))

Συζήτηση:
- ο GNB και η LR έχουν ακριβώς την ίδια επίδοση. Ο kNN έχει χειρότερο accuracy από τους άλλους δύο αλλά καλύτερο precision και recall στην κλάση 0. Γενικά δεν υπάρχει απαραίτητα μια συνολική, απόλυτη απάντηση για το ποιος είναι ο καλύτερος ταξινονητής σε ένα dataset.
- 1. Προεπεξεργασία: θα μπορούσαμε να δοκιμάσουμε και άλλες τεχνικές προεπεξεργασίας. Βέβαια, πρόκειται για ένα πολύ μικρό dataset και δεν πρέπει να περιμένουμε δραματικές αλλαγές. 
- 2. Υπερπαράμετροι: ο [GNB](https://scikit-learn.org/stable/modules/generated/sklearn.naive_bayes.GaussianNB.html) δεν έχει υπερπαραμέτρους προς βελτιστοποίηση. O [kNN](https://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html) έχει κάποιες, περιορισμένες στον αριθμό, όπως η `weights` και η `metric` που θα μπορούσαν να δοκιμαστούν. Η [λογιστική παλινδρόμηση](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html) έχει πολλές υπαρπαραμέτρους που μπορούν να δοκιμαστούν. Το πώς το κάνουμε αυτό, δηλαδή ποιο είναι το σωστό πρωτόκολλο εκτίμησης της απόδοσης τιμών περισσότερων υπερπαραμέτρων θα το δούμε στο επόμενο εργαστήριο.
